# Conjugate Gradient Algorithm

In [1]:
using LinearAlgebra
using Optim

Solve
$$
\min_x f(x) = \frac{1}{2} x^T A x + b^T x + a
$$
where $A \succ 0$. Setting $\nabla f(x) = 0$, it is equivalent to solve the linear system $Ax = -b$.

In [2]:
f = x -> 0.5*dot(x,A*x)+dot(b,x)

#3 (generic function with 1 method)

## A simple example

Adapted from https://www.rose-hulman.edu/~bryan/lottamath/congrad.pdf

Let
$$
A =
\begin{pmatrix}
3 & 1 & 0 \\
1 & 2 & 2 \\
0 & 2 & 4
\end{pmatrix}
$$
Consider the function to minimize
$$
f(x) = \frac{1}{2} x^TAx,
$$
and assume the we have already computed
\begin{align*}
d_0 &= (1, 0, 0)\\
d_1 & = (1, −3, 0)\\
d_2 &= (−2, 6, −5).
\end{align*}


Check that $d_0$, $d_1$ and $d_2$ are $A$-conjugate.

In [3]:
A = [ 3.0 1 0 ; 1 2 2 ; 0 2 4]
d0 = [ 1.0 0 0 ]'
d1 = [ 1.0 -3.0 0.0 ]'
d2 = [ -2.0 6.0 -5.0]'

println("$(dot(d0, A*d1)) $(dot(d0, A*d2)) $(dot(d1, A*d2))")

0.0 0.0 0.0


In [4]:
det(A), eigen(A)

(8.0, Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}([0.47108204270564347, 3.167449191108536, 5.361468766185826], [-0.3253061660474964 0.9167566816845831 0.23180397951318818; 0.8226726049360933 0.153510164791429 0.5473978574979729; -0.4662463763067133 -0.3687706819859466 0.804128410571644]))

Take initial guess $x_0 = (1, 2, 3)$. Compute $x_1$, $x_2$ and $x_3$ using the conjugate gradient algorithm. Is $x_3$ optimal?

$$
\nabla f(x) = Ax
$$

In [5]:
x0 = [1 2 3.0]'
-A*x0

3×1 Array{Float64,2}:
  -5.0
 -11.0
 -16.0

In [6]:
f = x -> dot(x,A*x)

#5 (generic function with 1 method)

We have to compute $\alpha_k$, $k = 1,2,3$, by solving
$$
\min_{\alpha} f(x_k + \alpha d_k)
$$

In order to obtain $\alpha_0$, we have to minimize
\begin{align*}
f(x_0 + \alpha d_0) &= \frac{1}{2}
\left(\begin{pmatrix} 1 & 2 & 3\end{pmatrix} + \alpha \begin{pmatrix} 1 & 0 & 0\end{pmatrix} \right)
\begin{pmatrix}
3 & 1 & 0 \\
1 & 2 & 2 \\
0 & 2 & 4
\end{pmatrix}
\left(\begin{pmatrix} 1 \\ 2 \\ 3 \end{pmatrix} + \alpha \begin{pmatrix} 1 \\0 \\0 \end{pmatrix} \right)
\\
& = \frac{1}{2}\begin{pmatrix} 1 + \alpha & 2 & 3 \end{pmatrix}
\begin{pmatrix}
3 & 1 & 0 \\
1 & 2 & 2 \\
0 & 2 & 4
\end{pmatrix}
\begin{pmatrix} 1 + \alpha \\ 2 \\ 3 \end{pmatrix}\\
& = \frac{1}{2}\begin{pmatrix} 1 + \alpha & 2 & 3 \end{pmatrix}
\begin{pmatrix} 5+3\alpha \\ 11+\alpha \\ 16 \end{pmatrix}\\
& = \frac{1}{2}
((1 + \alpha)(5+3\alpha) + 22+2\alpha + 48 ) \\
& = \frac{1}{2}
( 3\alpha^2 + 8\alpha + 5 + 70 + 2\alpha ) \\
& = \frac{3}{2}\alpha^2 + 5\alpha+\frac{75}{2}
\end{align*}
with respect to $\alpha$.

We can obtain it by searching the zero of the derivative with respect to $\alpha$, that is
$$
\frac{d}{d\alpha} f(x+\alpha d) = 0
$$

or

$$
d^T \nabla f(x+\alpha d) = 0
$$

Therefore, we must have

$$
3\alpha + 5 = 0
$$
Thus
$$
\alpha_{0} = -\frac{5}{3}
$$
$$
x_1 = x_0 - \frac{5}{3} d_0 = \begin{pmatrix} -\frac{2}{3} \\ 2 \\ 3  \end{pmatrix}
$$

We can also directly compute $\alpha_0$ as
$$
\alpha_0 = - \frac{d_0^T\nabla f(x_0)}{d_0^TAd_0}
$$

In [7]:
x0 = [1 ; 2 ; 3.0]
∇f = x -> A*x

#7 (generic function with 1 method)

In [8]:
d0 = [1 ; 0 ; 0]
α0 = -dot(d0,∇f(x0))/dot(d0,A*d0)

-1.6666666666666667

In [9]:
x1 = x0+α0*d0

3-element Array{Float64,1}:
 -0.6666666666666667
  2.0               
  3.0               

A linesearch from $x_1$ in direction $d_1$ requires us to minimize
$$
f(x_1 + \alpha d_1) = \frac{15}{2}\alpha^2 - 28\alpha + \frac{100}{3}
$$
which occurs at
$$
\alpha_1 = \frac{28}{15},
$$
yielding
$$
x_2 = x_1 + \frac{28}{15}d_1 =
    \begin{pmatrix}
     \frac{6}{5} \\ \frac{-18}{5} \\ 3
    \end{pmatrix}.
$$

In [10]:
α1 = -dot(d1,A*x1)/dot(d1,A*d1)

1.8666666666666665

In [11]:
28/15

1.8666666666666667

In [12]:
x2 = x1+α1*d1

3×1 Array{Float64,2}:
  1.1999999999999997
 -3.5999999999999996
  3.0               

The final linesearch from $x_2$ in direction $d_2$ requires us to minimize
$$
f(x_2 + \alpha d_2) = 20 \alpha^2 - 24\alpha + \frac{36}{5}
$$
which occurs at
$$
\alpha_2 = \frac{3}{5},
$$
yielding
$$
x_3 = x_2 + \frac{3}{5}d_2 =
    \begin{pmatrix}
     0 \\ 0 \\ 0
    \end{pmatrix},
$$
which is of course correct.

Similarly, we can compute the new point as

In [13]:
α2 = -dot(d2,A*x2)/dot(d2,A*d2)
x3 = x2+α2*d2

3×1 Array{Float64,2}:
 -4.440892098500626e-16
  8.881784197001252e-16
 -4.440892098500626e-16

## A naive implementation

A first version of the conjugate gradient algorithm follows.

In [14]:
function cg_quadratic(A:: Matrix, b:: Vector, x0:: Vector, trace:: Bool = false)
    n = length(x0)
    x = x0
    g = b+A*x
    d = -g
    if (trace)
        iter = [ x ]
        iterg = [ norm(g) ]
        iterd = [ norm(d) ]
    end
    k = 0
    
    for k = 1:n-1
        Ad = A*d
        normd = dot(d,Ad)
        α = -dot(d,g)/normd
        x += α*d
        if (trace)
            iter = [ iter; [x] ]
            iterg = [ iterg; norm(g)]
            iterd = [ iterd; norm(d) ]
        end
        g = b+A*x
        β = dot(g,Ad)/normd
        d = -g+β*d
    end

    normd = dot(d,A*d)
    α = -dot(d,g)/normd
    x += α*d
    if (trace)
        g = b+A*x # g must be equal to 0
        iter = [ iter; [x] ]
        iterg = [ iterg; norm(g)]
        iterd = [ iterd; norm(d) ]
        return x, iter, iterg, iterd
    end
    
    return x
end

cg_quadratic (generic function with 2 methods)

Consider the simple example

In [15]:
A = [2 1; 1 2]
b = [1, 0]
A\(-b)

2-element Array{Float64,1}:
 -0.6666666666666666
  0.3333333333333333

Solve
$$
    \min_{\alpha} f(x) = \frac{1}{2}x^TAx+b^Tx+c
$$

Or, equivalently, we solve
$$
    c+\min_{\alpha} f(x) = \frac{1}{2}x^TAx+b^Tx
$$

In [16]:
cg_quadratic(A, b, [0, 0], true)

([-0.6666666666666666, 0.3333333333333333], Array{Float64,1}[[0.0, 0.0], [-0.5, 0.0], [-0.6666666666666666, 0.3333333333333333]], [1.0, 1.0, 0.0], [1.0, 1.0, 0.5590169943749475])

What if $A$ is not positive definite?

In [17]:
A = [ 1 2 ; 2 1]
A\(-b)

2-element Array{Float64,1}:
  0.3333333333333333
 -0.6666666666666666

In [18]:
cg_quadratic(A, b, [0, 0], true)

([0.33333333333333326, -0.6666666666666666], Array{Float64,1}[[0.0, 0.0], [-1.0, 0.0], [0.33333333333333326, -0.6666666666666666]], [1.0, 1.0, 1.1102230246251565e-16], [1.0, 1.0, 4.47213595499958])

In [19]:
det(A)

-3.0

In [20]:
eigen(A)

Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}
eigenvalues:
2-element Array{Float64,1}:
 -1.0
  3.0
eigenvectors:
2×2 Array{Float64,2}:
 -0.707107  0.707107
  0.707107  0.707107

In [21]:
cg_quadratic(A, b, [1, 1], true)

([0.3333333333333335, -0.6666666666666667], Array{Float64,1}[[1.0, 1.0], [-0.36986301369863006, -0.02739726027397249], [0.3333333333333335, -0.6666666666666667]], [5.0, 5.0, 2.220446049250313e-16], [5.0, 5.0, 0.9763790695367754])

In [22]:
f([1/3,-2/3])

-0.3333333333333333

In [23]:
f([0,0])

0

The conjugate gradient finds the solution of the linear system, and this does correspond to a first-order critical point of the function.

In [24]:
∇f = x -> A*x+b

#9 (generic function with 1 method)

In [25]:
x = [1.0/3; -2.0/3]
∇f(x)

2-element Array{Float64,1}:
 0.0
 0.0

In [26]:
x = [1; 1]
∇f(x)

2-element Array{Int64,1}:
 4
 3

In [27]:
step= x -> x-α*∇f(x)

#11 (generic function with 1 method)

In [28]:
α = 10
dot(step(x),A*step(x))

6886

In [29]:
λ, u = eigen(A)

Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}
eigenvalues:
2-element Array{Float64,1}:
 -1.0
  3.0
eigenvectors:
2×2 Array{Float64,2}:
 -0.707107  0.707107
  0.707107  0.707107

In [30]:
u

2×2 Array{Float64,2}:
 -0.707107  0.707107
  0.707107  0.707107

In [31]:
x = u[:,1]
α = 10
f = x -> 0.5*dot(x,A*x)+dot(b,x)
f(step(x))

-106.05992052357223

In [32]:
α = 1000
dot(step(x),A*step(x))+dot(b,x)

-1.417629483042249e6

In [33]:
f(x)

-1.2071067811865475

In [34]:
x = [1/3.0; -2/3]
f(x)

0.16666666666666666

In [35]:
cg_quadratic(A, b, x, true)

([NaN, NaN], Array{Float64,1}[[0.3333333333333333, -0.6666666666666666], [NaN, NaN], [NaN, NaN]], [0.0, 0.0, NaN], [0.0, 0.0, NaN])

We will need to incorporate a test on $\nabla f(x_k)$!

In [36]:
A = [ 1 2 ; 0 4 ]
eigen(A)

Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}
eigenvalues:
2-element Array{Float64,1}:
 1.0
 4.0
eigenvectors:
2×2 Array{Float64,2}:
 1.0  0.5547 
 0.0  0.83205

In [37]:
eigen(A*A')

Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}
eigenvalues:
2-element Array{Float64,1}:
  0.7917560805262003
 20.2082439194738   
eigenvectors:
2×2 Array{Float64,2}:
 -0.885022  0.465549
  0.465549  0.885022

In [38]:
A = [ 3 1; 1 2 ]
eigen(A)

Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}
eigenvalues:
2-element Array{Float64,1}:
 1.381966011250105
 3.618033988749895
eigenvectors:
2×2 Array{Float64,2}:
  0.525731  -0.850651
 -0.850651  -0.525731

In [39]:
eigen(A*A')

Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}
eigenvalues:
2-element Array{Float64,1}:
  1.9098300562505257
 13.090169943749475 
eigenvectors:
2×2 Array{Float64,2}:
  0.525731  -0.850651
 -0.850651  -0.525731

A more complex example

In [40]:
n = 500;
m = 600;
A = randn(n,m);
A = A * A';  # A is now a positive semi-definite matrix
A = A+I # A is positive definite
b = zeros(n)
for i = 1:n
  b[i] = randn()
end
x0 = zeros(n)

500-element Array{Float64,1}:
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 ⋮  
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0

In [41]:
b1 = A\(-b)

500-element Array{Float64,1}:
  0.01597451883863155  
  0.028709623797665867 
 -0.03192775432385789  
  0.003984994205949193 
  0.011428678456896275 
  0.0027024152988841814
  0.04200549972597002  
 -0.014099307479139152 
  0.0021737037873165942
 -0.015045743623915846 
  0.013122422505916118 
 -0.01759605391997169  
  0.010265905433548106 
  ⋮                    
 -0.006276648826344925 
  0.010529080640319875 
  0.02598928757621842  
  0.023974826709166418 
 -0.005025111950753262 
 -0.016594864696717546 
  0.008055002833526772 
 -0.01638615916647562  
  0.02887626205712445  
  0.00349453613595297  
  0.011750890910482637 
  0.035641000732530244 

In [42]:
b2, iter, iterg, iterd = cg_quadratic(A, b, x0, true);

In [43]:
norm(b1-b2)

1.6153734771209275e-15

In [44]:
iterg

501-element Array{Float64,1}:
 22.32669327290362      
 22.32669327290362      
 20.50902419138704      
 18.944296782204336     
 17.18987841717313      
 15.301651241475364     
 13.353113615228848     
 12.00420404490857      
 10.728004847403112     
  9.683054723101787     
  9.007965176527785     
  7.881381957331188     
  6.642753666018093     
  ⋮                     
  1.305385865226395e-13 
  1.2093505031754848e-13
  1.2456336870192955e-13
  1.2068178785335202e-13
  1.1894716127871671e-13
  1.2428723655574613e-13
  1.192953141223575e-13 
  1.2271334977596007e-13
  1.2388924678227773e-13
  1.2191389512911638e-13
  1.309232564317756e-13 
  1.2340259757213947e-13

In [45]:
iterd

501-element Array{Float64,1}:
 22.32669327290362      
 22.32669327290362      
 27.84853046480883      
 30.388868610301273     
 30.356845010726595     
 28.50853006524143      
 25.487983877133125     
 23.841185386114986     
 21.855554380639635     
 20.267939081370205     
 19.718196114080804     
 17.028209112852267     
 13.800435529001483     
  ⋮                     
  1.3472809490517593e-13
  1.2561348952240697e-13
  1.2720738284692763e-13
  1.2631718703126367e-13
  1.182164287161592e-13 
  1.247567335462454e-13 
  1.1953452841602304e-13
  1.2460642630144355e-13
  1.2872594443046195e-13
  1.2869847664015946e-13
  1.374659971495118e-13 
  1.250566985805039e-13 

It works, but do we need to perform all the 500 iterations? We could be satisfied if we are close to the solution. We can mesure the residual of the linear system
$$
r = b+Ax
$$
that is nothing else the the gradient of the objective function of the quadratic optimization problem.

In [46]:
iter

501-element Array{Array{Float64,1},1}:
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]                                                                                                                                                                                                                                                                                                                                                                     
 [0.0002767606413135444, 0.0002733315138966624, -0.0010957482140589786, 0.00342103697035908, 0.0018584951036187565, 0.0017303923802678986, 0.0035685063965333794, 0.0015940332391309, 0.0016510508412575953, -0.0015997227786220224  …  0.0007459027881113781, 0.0015531034664322016, 0.0009448506398675648, 0.002238689009968792, 0.00021310327369990277, -0.00274278288496763, 0.0009802712223104066, 0.0019186132055392412, -0.0017158136204781266, 0.0018716526652683898]
 [0.0021490714058153616, 0.0007629911

We incorporate a convergence test in the function.

In [47]:
function cg_quadratic_tol(A:: Matrix, b:: Vector, x0:: Vector, trace:: Bool = false, tol = 1e-8)
    n = length(x0)
    x = x0
    if (trace)
        iter = [ x ]
    end
    g = b+A*x
    d = -g
    k = 0
    
    tol2 = tol*tol

    β = 0.0

    while ((dot(g,g) > tol2) && (k <= n))
        Ad = A*d
        normd = dot(d,Ad)
        α = dot(g,g)/normd
#        α = -dot(d,g)/normd
        x += α*d
        if (trace)
            iter = [ iter; x ]
        end
        g = b+A*x
        β = dot(g,Ad)/normd
        d = -g+β*d
        k += 1
    end

    if (trace)
        iter = [ iter; x ]
        return x, iter, k
    end

    return x, k
end

cg_quadratic_tol (generic function with 3 methods)

In [48]:
x, iter, k = cg_quadratic_tol(A, b, x0, true)

([0.01597451882112203, 0.028709623791649267, -0.03192775433157097, 0.003984994201861061, 0.0114286784498273, 0.002702415282237887, 0.042005499733811784, -0.014099307476687226, 0.0021737037789500433, -0.015045743622889955  …  0.02598928757205917, 0.02397482672012732, -0.005025111963837796, -0.016594864698436115, 0.008055002822780828, -0.01638615914812406, 0.028876262058443115, 0.0034945361401307992, 0.011750890910753055, 0.03564100073400417], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], 0.0002767606413135444, 0.0002733315138966624, -0.0010957482140589786, 0.00342103697035908, 0.0018584951036187565, 0.0017303923802678986, 0.0035685063965333794, 0.0015940332391309, 0.0016510508412575953  …  0.02598928757205917, 0.02397482672012732, -0.005025111963837796, -0.016594864698436115, 0.008055002822780828, -0.01638615914812406, 0.028876262058443115, 0.0034945361401307992, 0.011750890910753055, 0.03564100073400417], 193)

The number of iterations is

In [49]:
k

193

Are we close to the solution?

In [50]:
norm(b1-x)

2.2296899834490661e-10

In [51]:
size(A)

(500, 500)

which is much less than the problem dimension

## Preconditioned conjugate gradient

A basic implementation of a preconditioned conjugate gradient algorithm follows, were $M$ is the inverse of the preconditioner to apply.

In [53]:
function pcg_quadratic_tol(A:: Matrix, b:: Vector, x0:: Vector, M:: Matrix,
                           trace:: Bool = false, tol = 1e-8)
    n = length(x0)
    x = x0
    if (trace)
        iter = [ x ]
    end
    g = b+A*x
    v = M*g
    d = -v
    k = 0
    
    tol2 = tol*tol

    β = 0.0

    gv = dot(g,v)
    while ((gv > tol2) && (k <= n))
#    while ((dot(g,g) > tol2) && (k <= n))
        Ad = A*d
        normd = dot(d,Ad)
        #gv = dot(g,v)
        α = gv/normd
        x += α*d
        if (trace)
            iter = [ iter; x ]
        end
        g += α*Ad
        v = M*g
        gvold = gv
        gv = dot(g,v)
        β = gv/gvold
        d = -v+β*d
        k += 1
    end

    if (trace)
        iter = [ iter; x ]
        return x, iter, k
    end

    return x, k
end

pcg_quadratic_tol (generic function with 3 methods)

Let's check first that when there is no preconditioning, we obtain the same iterates.
Set

In [54]:
M = zeros(n,n)+I
x, iter, k = pcg_quadratic_tol(A, b, x0, M, true)

([0.015974518821207862, 0.028709623792143396, -0.031927754330216294, 0.003984994202316493, 0.011428678450270907, 0.0027024152828897534, 0.04200549973349374, -0.014099307476557727, 0.0021737037797074257, -0.015045743623517504  …  0.025989287572569776, 0.02397482672008192, -0.005025111963021935, -0.01659486469889695, 0.008055002822959107, -0.01638615914854714, 0.02887626205801894, 0.0034945361396659463, 0.011750890910751113, 0.03564100073428025], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], 0.0002767606413135444, 0.0002733315138966624, -0.0010957482140589786, 0.00342103697035908, 0.0018584951036187565, 0.0017303923802678986, 0.0035685063965333794, 0.0015940332391309, 0.0016510508412575953  …  0.025989287572569776, 0.02397482672008192, -0.005025111963021935, -0.01659486469889695, 0.008055002822959107, -0.01638615914854714, 0.02887626205801894, 0.0034945361396659463, 0.011750890910751113, 0.03564100073428025], 191)

In [55]:
k, norm(x-b1)

(191, 2.1840922688602002e-10)

We can compute the eigenvalues and condition number of $A$.

In [56]:
eigen(A)

Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}
eigenvalues:
500-element Array{Float64,1}:
    5.6347873665070125
    6.568444017779966 
    7.489746666278461 
    7.844986364490883 
    8.161787767359893 
    8.694467252631284 
    9.013297019850604 
   10.122452124852767 
   10.447788330344956 
   11.64997528781129  
   12.091908992319638 
   13.294468830274475 
   13.420305154608918 
    ⋮                 
 1920.9222115923171   
 1946.2393789278747   
 1954.906424415574    
 1990.7946362198902   
 2006.3267494852591   
 2019.6958115404982   
 2023.013770835366    
 2056.7645567980553   
 2070.654706568727    
 2119.4968773451974   
 2160.4366473431965   
 2208.6742110658283   
eigenvectors:
500×500 Array{Float64,2}:
 -0.0108411    0.0830059    0.0337321   …   0.00544394   -0.0368143  
 -0.0166809    0.037664     0.00301322     -0.0647637     0.00924254 
 -0.0109104   -0.0298255    0.0202361      -0.0166545     0.0450626  
 -0.0260085   -0.0357509    0.0126751       0.041804

In [57]:
cond(A)

391.9711725404463

Try to compute a simple precontionner using the inverse of the diagonal of matrix $A$.

In [58]:
D = 1 ./diag(A)
M = Diagonal(D)

500×500 Diagonal{Float64,Array{Float64,1}}:
 0.00180538   ⋅           ⋅          …   ⋅           ⋅           ⋅        
  ⋅          0.00162809   ⋅              ⋅           ⋅           ⋅        
  ⋅           ⋅          0.00166734      ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅              ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅              ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅          …   ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅              ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅              ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅              ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅              ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅          …   ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅              ⋅           ⋅           ⋅        
  ⋅           ⋅           ⋅              ⋅           ⋅  

Unfortunately, in this case, it does not help as the condition number is not improving.

In [60]:
B = M*A
cond(B)

392.7861780853309

Consider another situation when $A$ is diagonal.

In [61]:
n = 1000;
A = zeros(n,n);
for i = 1:n
    A[i,i] = 10*rand()
end
b = zeros(n)
for i = 1:n
  b[i] = rand()
end
x0 = zeros(n)
cond(A)

573.7929667509559

The solution we are looking for is

In [62]:
A\b

1000-element Array{Float64,1}:
 0.08511153833584434  
 0.0006468123709911861
 1.0013983310364591   
 0.16609043417698013  
 0.06556649716468967  
 0.053305142501921275 
 0.1330303200775495   
 0.07521223614895942  
 0.07434309714215172  
 0.11919717174421243  
 0.3395450294971931   
 0.04731761256378243  
 0.12257493102570208  
 ⋮                    
 0.13967384586652654  
 0.1994659576124026   
 0.20576921142916305  
 0.03653041453119203  
 0.12633530344223995  
 0.16457566391926592  
 0.1860308402751664   
 0.23193104246255242  
 0.14603650854633932  
 0.09020585221888404  
 0.04861227773813524  
 0.031573428647867274 

Without preconditionning, with have the iterates sequence

In [63]:
M = zeros(n,n)+I
x, iter, k = pcg_quadratic_tol(A, b, x0, M, true)

([-0.0851115383358446, -0.0006468123709942869, -1.0013983311042045, -0.16609043419701267, -0.06556649715409481, -0.05330514259925526, -0.13303032010196264, -0.07521223610378068, -0.07434309714948052, -0.11919717177496945  …  -0.2057692115018965, -0.036530414509147145, -0.12633530342222551, -0.1645756638529031, -0.18603084046921495, -0.2319310422065388, -0.1460365084758426, -0.09020585223805899, -0.048612277779012024, -0.031573428667768966], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.16771570209428255, -0.0012785774778700473, -0.17187852852030042, -0.17944655439538684, -0.11900440761468015, -0.10204472832347751, -0.1746280084912797, -0.057858758881205334, -0.08306066632162536  …  -0.2057692115018965, -0.036530414509147145, -0.12633530342222551, -0.1645756638529031, -0.18603084046921495, -0.2319310422065388, -0.1460365084758426, -0.09020585223805899, -0.048612277779012024, -0.031573428667768966], 182)

This is equivalent to the unpreconditioned version.

In [64]:
x, iter, k = cg_quadratic_tol(A, b, x0, true)

([-0.08511153833584394, -0.000646812370994591, -1.0013983311042047, -0.16609043419701278, -0.06556649715409484, -0.05330514259925528, -0.13303032010196272, -0.07521223610378056, -0.0743430971494805, -0.11919717177496944  …  -0.20576921150189653, -0.03653041450914715, -0.12633530342222543, -0.16457566385290312, -0.18603084046921484, -0.23193104220653885, -0.1460365084758425, -0.09020585223805905, -0.04861227777901204, -0.031573428667768924], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.16771570209428255, -0.0012785774778700473, -0.17187852852030042, -0.17944655439538684, -0.11900440761468015, -0.10204472832347751, -0.1746280084912797, -0.057858758881205334, -0.08306066632162536  …  -0.20576921150189653, -0.03653041450914715, -0.12633530342222543, -0.16457566385290312, -0.18603084046921484, -0.23193104220653885, -0.1460365084758425, -0.09020585223805905, -0.04861227777901204, -0.031573428667768924], 182)

However, since $A$ is diagonal, an obvious diagonal preconditionner is $A^{-1}$ itself.

In [65]:
M = zeros(n,n)
for i = 1:n
    M[i,i] = 1/A[i,i]
end

The condition number of the preconditioned matrix is of course equal to 1.

In [66]:
cond(M*A)

1.0000000000000002

The theory then predicts that we converge in one iteration with the precionditionned conjugate gradient.

In [67]:
x, iter, k = pcg_quadratic_tol(A, b, x0, M, true)

([-0.08511153833584435, -0.0006468123709911862, -1.0013983310364591, -0.1660904341769802, -0.06556649716468968, -0.053305142501921296, -0.1330303200775495, -0.07521223614895943, -0.07434309714215173, -0.11919717174421246  …  -0.20576921142916313, -0.03653041453119204, -0.12633530344223998, -0.16457566391926595, -0.18603084027516642, -0.23193104246255247, -0.14603650854633934, -0.09020585221888405, -0.04861227773813525, -0.03157342864786728], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.08511153833584435, -0.0006468123709911862, -1.0013983310364591, -0.1660904341769802, -0.06556649716468968, -0.053305142501921296, -0.1330303200775495, -0.07521223614895943, -0.07434309714215173  …  -0.20576921142916313, -0.03653041453119204, -0.12633530344223998, -0.16457566391926595, -0.18603084027516642, -0.23193104246255247, -0.14603650854633934, -0.09020585221888405, -0.04861227773813525, -0.03157342864786728], 1)

Consider now another example.

In [68]:
A = zeros(n,n)+3*I
for i = 1:n-1
    A[i,i+1] = 1.4
    A[i+1,i] = 1.4
end
A

1000×1000 Array{Float64,2}:
 3.0  1.4  0.0  0.0  0.0  0.0  0.0  0.0  …  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 1.4  3.0  1.4  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  1.4  3.0  1.4  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  1.4  3.0  1.4  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  1.4  3.0  1.4  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  1.4  3.0  1.4  0.0  …  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  1.4  3.0  1.4     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  1.4  3.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.4     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  …  0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0  0.0  0.0
 0.0  0.0  0.0  0.0  0.0  0.0  0.0  

In [69]:
eigen(A)

Eigen{Float64,Float64,Array{Float64,2},Array{Float64,1}}
eigenvalues:
1000-element Array{Float64,1}:
 0.20001378984134793
 0.20005515922956107
 0.20012410775715758
 0.20022063474500001
 0.20034473924231072
 0.2004964200266737 
 0.2006756756040492 
 0.20088250420879217
 0.20111690380366315
 0.20137887207985267
 0.20166840645700262
 0.20198550408323332
 0.20233016183516794
 ⋮                  
 5.7980144959167665 
 5.798331593542997  
 5.798621127920147  
 5.798883096196337  
 5.799117495791208  
 5.7993243243959505 
 5.799503579973327  
 5.79965526075769   
 5.799779365255     
 5.799875892242843  
 5.799944840770439  
 5.799986210158653  
eigenvectors:
1000×1000 Array{Float64,2}:
 -0.000140286  -0.00028057   -0.000420851  …   0.00028057   0.000140286
  0.00028057    0.000561129   0.000841665      0.000561129  0.00028057 
 -0.000420851  -0.000841665  -0.0012624        0.000841665  0.000420851
  0.000561129   0.00112217    0.00168303       0.00112217   0.000561129
 -0.0007014    -0.00140

In [70]:
A\(-b)

1000-element Array{Float64,1}:
 -0.5302289407584934 
  0.5320572116235507 
 -0.614499363830206  
  0.16558409106245517
 -0.3867283770710757 
  0.23444036479376498
 -0.48323066739804693
  0.17200666195791722
 -0.09377460297319108
 -0.2702632857913654 
  0.07743925607339158
 -0.24311535606791693
  0.11472168208891691
  ⋮                  
  0.33685798270574924
 -0.41825398526282176
 -0.11951583027789782
  0.20944855966974235
 -0.4354505818938196 
  0.19390325946301898
 -0.37979197192850783
  0.3177259668162186 
 -0.5326302518132492 
  0.12218995452625997
 -0.15109683644442018
 -0.02980410623663226

In [71]:
x, iter, k = cg_quadratic_tol(A, b, x0, true)

([-0.5302289403705569, 0.5320572110460983, -0.6144993633198529, 0.16558409070301935, -0.3867283766906912, 0.2344403645353679, -0.48323066718196606, 0.17200666191450553, -0.09377460293883143, -0.2702632857715988  …  -0.11951582966392606, 0.2094485592538897, -0.43545058159381483, 0.19390325943627734, -0.3797919719216848, 0.31772596691149946, -0.5326302519660845, 0.12218995462017966, -0.15109683666282, -0.029804106119259707], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.16529460248077343, -0.001260120270829454, -0.16939733544311864, -0.17685611129395332, -0.11728649139285964, -0.10057163755606846, -0.17210712464685335, -0.05702352510752649, -0.08186162446318297  …  -0.11951582966392606, 0.2094485592538897, -0.43545058159381483, 0.19390325943627734, -0.3797919719216848, 0.31772596691149946, -0.5326302519660845, 0.12218995462017966, -0.15109683666282, -0.029804106119259707], 56)

In [72]:
M = zeros(n,n)
for i = 1:n
    M[i,i] = 1/A[i,i]
end

In [73]:
cond(A)

28.997931666407833

In [74]:
cond(M*A)

28.997931666407865

In [75]:
x, iter, k = pcg_quadratic_tol(A, b, x0, M, true)

([-0.5302289402041654, 0.5320572109436659, -0.6144993631382352, 0.1655840901811337, -0.386728376366776, 0.234440364226002, -0.4832306671692573, 0.1720066621540863, -0.09377460338549971, -0.2702632856365679  …  -0.11951582981798614, 0.209448559167586, -0.43545058168730405, 0.19390325937609734, -0.3797919723525358, 0.3177259673524759, -0.5326302520995585, 0.12218995472152971, -0.15109683643578578, -0.029804106122671817], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.16529460248077343, -0.0012601202708294541, -0.16939733544311866, -0.17685611129395334, -0.11728649139285965, -0.10057163755606847, -0.17210712464685338, -0.05702352510752649, -0.08186162446318297  …  -0.11951582981798614, 0.209448559167586, -0.43545058168730405, 0.19390325937609734, -0.3797919723525358, 0.3177259673524759, -0.5326302520995585, 0.12218995472152971, -0.15109683643578578, -0.029804106122671817], 55)

There is no advantage.

In [76]:
M = A^(-1)

1000×1000 Array{Float64,2}:
  0.490553      -0.336899       0.231373      …   5.26731e-164  -2.45808e-164
 -0.336899       0.721926      -0.4958           -1.12871e-163   5.26731e-164
  0.231373      -0.4958         0.831055          1.89193e-163  -8.82901e-164
 -0.158901       0.340503      -0.570747         -2.92543e-163   1.3652e-163 
  0.109129      -0.233848       0.391974          4.37685e-163  -2.04253e-163
 -0.0749471      0.160601      -0.269198      …  -6.45353e-163   3.01165e-163
  0.0514717     -0.110297       0.184878          9.45214e-163  -4.411e-163  
 -0.0353494      0.0757488     -0.126969         -1.38011e-162   6.44049e-163
  0.0242771     -0.0520223      0.0871993         2.01216e-162  -9.39006e-163
 -0.0166729      0.0357276     -0.0598862        -2.93166e-162   1.36811e-162
  0.0114505     -0.0245368      0.0411283     …   4.26996e-162  -1.99265e-162
 -0.00786389     0.0168512     -0.0282458        -6.21827e-162   2.90186e-162
  0.00540072    -0.011573       0.01

In [77]:
x, iter, k = pcg_quadratic_tol(A, b, x0, M, true)

([-0.5302289407584935, 0.5320572116235506, -0.6144993638302059, 0.16558409106245536, -0.386728377071076, 0.23444036479376512, -0.48323066739804726, 0.17200666195791728, -0.09377460297319118, -0.27026328579136544  …  -0.1195158302778978, 0.20944855966974238, -0.4354505818938197, 0.19390325946301892, -0.379791971928508, 0.31772596681621873, -0.5326302518132492, 0.12218995452626004, -0.1510968364444202, -0.029804106236632273], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.5302289407584935, 0.5320572116235506, -0.6144993638302059, 0.16558409106245536, -0.386728377071076, 0.23444036479376512, -0.48323066739804726, 0.17200666195791728, -0.09377460297319118  …  -0.1195158302778978, 0.20944855966974238, -0.4354505818938197, 0.19390325946301892, -0.379791971928508, 0.31772596681621873, -0.5326302518132492, 0.12218995452626004, -0.1510968364444202, -0.029804106236632273], 1)

Consider now the following example.

In [78]:
n = 1000
A = zeros(n,n)+Diagonal([2+i*i for i=1:n])

1000×1000 Array{Float64,2}:
 3.0  0.0   0.0   0.0   0.0   0.0  …       0.0       0.0       0.0  0.0  
 0.0  6.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0  11.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0  18.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0  27.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0  38.0  …       0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0  …       0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 ⋮        

In [79]:
for i = 1:n-1
    A[i,i+1] = 1
    A[i+1,i] = 1
end
A[n,1] = 1
A[1,n] = 1
cond(A)

372201.88311699365

In [80]:
A

1000×1000 Array{Float64,2}:
 3.0  1.0   0.0   0.0   0.0   0.0  …       0.0       0.0       0.0  1.0  
 1.0  6.0   1.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  1.0  11.0   1.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   1.0  18.0   1.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   1.0  27.0   1.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   1.0  38.0  …       0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   1.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0  …       0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 0.0  0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  0.0  
 ⋮        

In [81]:
κ = cond(A)
(sqrt(κ)-1)/(sqrt(κ)+1)

0.9967271248797949

In [82]:
A^(-1)

1000×1000 Array{Float64,2}:
  0.353263     -0.0597876     0.00546288   …   3.53969e-13  -3.53262e-7 
 -0.0597876     0.179363     -0.0163886       -5.99071e-14   5.97875e-8 
  0.00546288   -0.0163886     0.092869         5.4738e-15   -5.46287e-9 
 -0.00030412    0.000912359  -0.00517004      -3.04728e-16   3.04119e-10
  1.12747e-5   -3.38241e-5    0.00019167       1.12972e-17  -1.12747e-11
 -2.96856e-7    8.90567e-7   -5.04654e-6   …  -2.97449e-19   2.96855e-13
  5.82243e-9   -1.74673e-8    9.89813e-8       5.83407e-21  -5.82242e-15
 -8.82347e-11   2.64704e-10  -1.49999e-9      -8.84111e-23   8.82346e-17
  1.06319e-12  -3.18958e-12   1.80743e-11      1.06532e-24  -1.06319e-18
 -1.04243e-14   3.12729e-14  -1.77213e-13     -1.04451e-26   1.04243e-20
  8.47552e-17  -2.54265e-16   1.44084e-15  …   8.49246e-29  -8.4755e-23 
 -5.80538e-19   1.74161e-18  -9.86915e-18     -5.81699e-31   5.80537e-25
  3.39506e-21  -1.01852e-20   5.7716e-20       3.40185e-33  -3.39505e-27
  ⋮                    

In [83]:
M = zeros(n,n)+I
x, iter, k = pcg_quadratic_tol(A, b, x0, M, true)

([-0.3033119021203991, 0.05994014657633306, -0.08001978468687258, -0.04422351949800128, -0.02095934787711228, -0.011914718169687078, -0.017020464511779073, -0.004390717558910035, -0.004772806836022754, -0.00802569923839308  …  -5.223710448619647e-7, -1.5112923825799127e-7, -7.521537523920856e-7, -5.667000138195912e-7, -4.6473990358393947e-7, -3.266710880132152e-7, -9.8792630635204e-7, -5.929959676495789e-7, -3.2468772915646726e-7, -1.7702498323373305e-7], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -2.4915369033636528e-6, -1.8994184385502717e-8, -2.5533786721021e-6, -2.665807118084986e-6, -1.767895727904024e-6, -1.5159475423996675e-6, -2.5942241667529414e-6, -8.595333122375362e-7, -1.2339257014943442e-6  …  -5.223710448619647e-7, -1.5112923825799127e-7, -7.521537523920856e-7, -5.667000138195912e-7, -4.6473990358393947e-7, -3.266710880132152e-7, -9.8792630635204e-7, -5.929959676495789e-7, -3.2468772915646726e-7, -1.7702498

In [86]:
M = zeros(n,n)
for i = 1:n
    M[i,i] = 1/A[i,i]
end
cond(A*M), cond(A)

(1.926360732450869, 372201.88311699365)

In [87]:
M

1000×1000 Array{Float64,2}:
 0.333333  0.0       0.0        …  0.0         0.0       0.0       
 0.0       0.166667  0.0           0.0         0.0       0.0       
 0.0       0.0       0.0909091     0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0        …  0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0        …  0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 ⋮                              ⋱                                  
 0.0       0.0      

In [88]:
A*M

1000×1000 Array{Float64,2}:
 1.0       0.166667  0.0        …  0.0         0.0       9.99998e-7
 0.333333  1.0       0.0909091     0.0         0.0       0.0       
 0.0       0.166667  1.0           0.0         0.0       0.0       
 0.0       0.0       0.0909091     0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0        …  0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0        …  0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 0.0       0.0       0.0           0.0         0.0       0.0       
 ⋮                              ⋱                                  
 0.0       0.0      

In [89]:
x, iter, k = pcg_quadratic_tol(A, b, x0, M, true)

([-0.30287293549210814, 0.06281207850145543, -0.08044752709136636, -0.04468954806074069, -0.02010717159693447, -0.012567712035396262, -0.016941340441385185, -0.004090090650218402, -0.004900069594150625, -0.008087212138416136  …  -6.627484313750857e-7, -1.5101211052488287e-7, -7.52150227113502e-7, -5.664039430184978e-7, -4.2735612965806707e-7, -3.2682047950118643e-7, -9.879242267200632e-7, -5.930152520612125e-7, -3.2459795367496876e-7, 1.9253629660874997e-9], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.27402478474876785, -0.0010445113778345088, -0.07658898555859281, -0.04886523526427786, -0.021604123839437214, -0.013162680889718684, -0.01678344464520518, -0.004296972292525528, -0.004905177119258366  …  -6.627484313750857e-7, -1.5101211052488287e-7, -7.52150227113502e-7, -5.664039430184978e-7, -4.2735612965806707e-7, -3.2682047950118643e-7, -9.879242267200632e-7, -5.930152520612125e-7, -3.2459795367496876e-7, 1.925362966

In [90]:
function pcg_quadratic(A:: Matrix, b:: Vector, x0:: Vector, M:: Matrix,
                       trace:: Bool = false, tol = 1e-8)
    n = length(x0)
    x = x0
    if (trace)
        iter = [ x ]
    end
    g = b+A*x
    v = M\g
    d = -v
    k = 0
    
    tol2 = tol*tol

    β = 0.0

    gv = dot(g,v)
    while ((gv > tol2) && (k <= n))
#    while ((dot(g,g) > tol2) && (k <= n))
        Ad = A*d
        normd = dot(d,Ad)
        #gv = dot(g,v)
        α = gv/normd
        x += α*d
        if (trace)
            iter = [ iter; x ]
        end
        g += α*Ad
        v = M\g
        gvold = gv
        gv = dot(g,v)
        β = gv/gvold
        d = -v+β*d
        k += 1
    end

    if (trace)
        iter = [ iter; x ]
        return x, iter, k
    end

    return x, k
end

pcg_quadratic (generic function with 3 methods)

Adapted from https://en.wikipedia.org/wiki/Incomplete_Cholesky_factorization

In [91]:
function ichol(A:: Matrix)

    n = size(A,1)
    C = zeros(n,n)+I
    
    for k=1:n
        C[k,k] = sqrt(A[k,k])
        for i=(k+1):n
            if (A[i,k] != 0)
                C[i,k] = A[i,k]/A[k,k]    
            end
        end
        for j=(k+1):n
            for i=j:n
                if (A[i,j] != 0)
                    C[i,j] = A[i,j]-A[i,k]*A[j,k]
                end
            end
        end
    end

    return C
end

ichol (generic function with 1 method)

In [92]:
C = cholesky(A)
C.L

1000×1000 LowerTriangular{Float64,Array{Float64,2}}:
 1.73205    ⋅         ⋅          ⋅          …     ⋅           ⋅            ⋅ 
 0.57735   2.38048    ⋅          ⋅                ⋅           ⋅            ⋅ 
 0.0       0.420084  3.28991     ⋅                ⋅           ⋅            ⋅ 
 0.0       0.0       0.303959   4.23174           ⋅           ⋅            ⋅ 
 0.0       0.0       0.0        0.23631           ⋅           ⋅            ⋅ 
 0.0       0.0       0.0        0.0         …     ⋅           ⋅            ⋅ 
 0.0       0.0       0.0        0.0               ⋅           ⋅            ⋅ 
 0.0       0.0       0.0        0.0               ⋅           ⋅            ⋅ 
 0.0       0.0       0.0        0.0               ⋅           ⋅            ⋅ 
 0.0       0.0       0.0        0.0               ⋅           ⋅            ⋅ 
 0.0       0.0       0.0        0.0         …     ⋅           ⋅            ⋅ 
 0.0       0.0       0.0        0.0               ⋅           ⋅            ⋅ 
 0.0       

In [93]:
M = C.L*C.U

1000×1000 Array{Float64,2}:
 3.0   1.0          0.0          …       0.0       0.0   1.0        
 1.0   6.0          1.0                  0.0       0.0   0.0        
 0.0   1.0         11.0                  0.0       0.0   0.0        
 0.0   0.0          1.0                  0.0       0.0  -8.67362e-19
 0.0   0.0          0.0                  0.0       0.0   0.0        
 0.0   0.0          0.0          …       0.0       0.0   0.0        
 0.0   0.0          0.0                  0.0       0.0   0.0        
 0.0   0.0          0.0                  0.0       0.0   0.0        
 0.0   0.0          0.0                  0.0       0.0   0.0        
 0.0   0.0          0.0                  0.0       0.0   0.0        
 0.0   0.0          0.0          …       0.0       0.0   0.0        
 0.0   0.0          0.0                  0.0       0.0   1.2326e-32 
 0.0   0.0          0.0                  0.0       0.0   0.0        
 ⋮                               ⋱                                  
 0.0  

In [94]:
x, iter, k = pcg_quadratic(A, b, x0, M, true)

([-0.302872935477591, 0.0628120785048972, -0.08044752710531945, -0.04468954807659282, -0.02010717159043811, -0.012567711996097228, -0.016941340433343832, -0.004090090645152937, -0.004900069632543694, -0.008087212140121163  …  -6.627484294845439e-7, -1.5101211009477288e-7, -7.521502249676146e-7, -5.664039414029092e-7, -4.27356128439094e-7, -3.268204785693923e-7, -9.879242239014944e-7, -5.930152503697571e-7, -3.2459795274953857e-7, 1.9253664927258085e-9], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.302872935477591, 0.0628120785048972, -0.08044752710531945, -0.04468954807659282, -0.02010717159043811, -0.012567711996097228, -0.016941340433343832, -0.004090090645152937, -0.004900069632543694  …  -6.627484294845439e-7, -1.5101211009477288e-7, -7.521502249676146e-7, -5.664039414029092e-7, -4.27356128439094e-7, -3.268204785693923e-7, -9.879242239014944e-7, -5.930152503697571e-7, -3.2459795274953857e-7, 1.9253664927258085e-9], 

In [95]:
C = ichol(A)

1000×1000 Array{Float64,2}:
 1.73205   0.0       0.0        …    0.0           0.0          0.0
 0.333333  2.44949   0.0             0.0           0.0          0.0
 0.0       0.166667  3.31662         0.0           0.0          0.0
 0.0       0.0       0.0909091       0.0           0.0          0.0
 0.0       0.0       0.0             0.0           0.0          0.0
 0.0       0.0       0.0        …    0.0           0.0          0.0
 0.0       0.0       0.0             0.0           0.0          0.0
 0.0       0.0       0.0             0.0           0.0          0.0
 0.0       0.0       0.0             0.0           0.0          0.0
 0.0       0.0       0.0             0.0           0.0          0.0
 0.0       0.0       0.0        …    0.0           0.0          0.0
 0.0       0.0       0.0             0.0           0.0          0.0
 0.0       0.0       0.0             0.0           0.0          0.0
 ⋮                              ⋱                                  
 0.0       0.0      

In [96]:
M=C*C'

1000×1000 Array{Float64,2}:
 3.0      0.57735    0.0        0.0       …       0.0       0.57735 
 0.57735  6.11111    0.408248   0.0               0.0       0.111111
 0.0      0.408248  11.0278     0.301511          0.0       0.0     
 0.0      0.0        0.301511  18.0083            0.0       0.0     
 0.0      0.0        0.0        0.235702          0.0       0.0     
 0.0      0.0        0.0        0.0       …       0.0       0.0     
 0.0      0.0        0.0        0.0               0.0       0.0     
 0.0      0.0        0.0        0.0               0.0       0.0     
 0.0      0.0        0.0        0.0               0.0       0.0     
 0.0      0.0        0.0        0.0               0.0       0.0     
 0.0      0.0        0.0        0.0       …       0.0       0.0     
 0.0      0.0        0.0        0.0               0.0       0.0     
 0.0      0.0        0.0        0.0               0.0       0.0     
 ⋮                                        ⋱                         
 0.0  

In [97]:
x, iter, k = pcg_quadratic(A, b, x0, M, true)

([-0.3028729348712248, 0.06281207863588409, -0.08044752743781927, -0.0446895483119123, -0.020107171544602988, -0.012567712048556683, -0.01694134006428405, -0.004090090604532912, -0.004900069536930813, -0.008087212162320046  …  -6.627484390001745e-7, -1.510121122626337e-7, -7.521502357670275e-7, -5.66403949535178e-7, -4.2735613457495256e-7, -3.268204832615723e-7, -9.87924238086172e-7, -5.930152588840834e-7, -3.245979574089855e-7, 1.9253587148019873e-9], Any[[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0  …  0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], -0.28970488296005, 0.031579682453543666, -0.07890400459005509, -0.048947519530897765, -0.021835610398601116, -0.013438943873607213, -0.017316518104116798, -0.004401349104935594, -0.005059666033730756  …  -6.627484390001745e-7, -1.510121122626337e-7, -7.521502357670275e-7, -5.66403949535178e-7, -4.2735613457495256e-7, -3.268204832615723e-7, -9.87924238086172e-7, -5.930152588840834e-7, -3.245979574089855e-7, 1.9253587148019873e-9], 

An efficient implementation would make use of sparse matrices and specific functions to compute v.

In [109]:
for i = 1:n-1
    A[i,i+1] = 1
    A[i+1,i] = 1
end
for i = 1:10000
    j = Int(ceil(rand()*1000))
    A[n,j] = 5
    A[j,n] = 5
end
cond(A)

302408.83092529565

In [110]:
A

1000×1000 Array{Float64,2}:
 3.0  1.0   0.0   0.0   0.0   0.0   0.0  …       0.0       0.0       0.0  5.0
 1.0  6.0   1.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  5.0
 0.0  1.0  11.0   1.0   0.0   0.0   0.0          0.0       0.0       0.0  5.0
 0.0  0.0   1.0  18.0   1.0   0.0   0.0          0.0       0.0       0.0  5.0
 0.0  0.0   0.0   1.0  27.0   1.0   0.0          0.0       0.0       0.0  5.0
 0.0  0.0   0.0   0.0   1.0  38.0   1.0  …       0.0       0.0       0.0  5.0
 0.0  0.0   0.0   0.0   0.0   1.0  51.0          0.0       0.0       0.0  5.0
 0.0  0.0   0.0   0.0   0.0   0.0   1.0          0.0       0.0       0.0  5.0
 0.0  0.0   0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  5.0
 0.0  0.0   0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  5.0
 0.0  0.0   0.0   0.0   0.0   0.0   0.0  …       0.0       0.0       0.0  5.0
 0.0  0.0   0.0   0.0   0.0   0.0   0.0          0.0       0.0       0.0  5.0
 0.0  0.0   0.0   0.0   0.0   0.0   

In [111]:
C = cholesky(A)
C.L

PosDefException: PosDefException: matrix is not positive definite; Cholesky factorization failed.